In [1]:
import numpy as np

In [2]:
class history:
    def __init__(self):
        self.step = 0
        self.capture_positions = {}
        self.move_positions = {}
        self.final_position = {}
        self.board = {}
        
    def add(self, capture_positions, move_positions, final_position, new=True):
        if new == True:
            self.capture_positions[self.step] = capture_positions
            self.move_positions[self.step] = move_positions
            self.final_position[self.step] = final_position
            self.step = self.step + 1
        else:
            self.capture_positions[self.step-1].append(capture_positions)
            self.move_positions[self.step-1].append(move_positions)
            self.move_positions[self.step-1].append(self.final_position[self.step-1])
            self.final_position[self.step-1] = final_position
    
    def save_board(self, board):
        self.board[self.step-1] = board

In [3]:
class piece:
    def __init__(self, ind, position, is_b, symbol, live=True, priority=False, moves=[], is_king=False):
        self.id = ind
        self.position = position
        self.is_b = is_b
        self.symbol = symbol
        self.live = live
        self.priority = priority
        self.moves = moves
        self.is_king = is_king
        

In [4]:
class checkers:
    def __init__(self):
        shape = (8,8)
        ids = 0
        self.pieces = {}
        self.history = history()
        
        for i in range(shape[0]):
            for j in range(shape[1]):
                if i<3 and ((i%2 == 1 and j%2 == 0) or (i%2 == 0 and j%2 == 1)):
                    self.pieces[ids] = piece(ids, (i,j), False, 'r')
                    ids += 1
                elif i>shape[1]-4 and ((i%2 == 1 and j%2 == 0) or (i%2 == 0 and j%2 == 1)):
                    self.pieces[ids] = piece(ids, (i,j), True, 'b')
                    ids += 1
                    
        self.update_board()
        self.b_turn = True
        self.free_moves()
        
    def move_this(self, action):
        if action != None:
            i, j = action
            recent_move = []
            recent_capture = []

            capture = False

            moves = self.pieces[i].moves
            
            if len(moves) > 0:
                if self.pieces[i].priority:
        #                 print('jump')
                    enemy_x = (self.pieces[i].position[0]+moves[j][0])/2
                    enemy_y = (self.pieces[i].position[1]+moves[j][1])/2
                    capture = True
                    recent_capture.append((enemy_x, enemy_y))
                    for k,v in self.pieces.items():
                        if (enemy_x, enemy_y) == v.position:
                            v.live = False
                            v.position = (-1,-1)
                            v.moves = []

                recent_move.append(self.pieces[i].position)
#                 print(j, moves)
                self.history.add(recent_capture, recent_move, moves[j])

                self.pieces[i].position = moves[j]
                if self.pieces[i].is_b and self.pieces[i].position[0] == 0:
        #                 print('king!')
                    self.pieces[i].is_king = True
                    self.pieces[i].symbol = 'B'
                if not self.pieces[i].is_b and self.pieces[i].position[0] == 7:
        #                 print('king!')
                    self.pieces[i].is_king = True
                    self.pieces[i].symbol = 'R'

                self.update_board()
                can_move = self.free_moves()

                if not(capture and self.pieces[i].priority):
    #                 print('change turn')
                    self.b_turn = not self.b_turn
                    self.history.save_board(self.board)
                    can_move = self.free_moves()

                return ("".join(self.board.reshape(-1)), 0.0, False)
            
            else:
                reward = 1.0
                if self.b_turn:
                    reward = -1.0
                return ("".join(self.board.reshape(-1)), reward, True)
            
        else:
            reward = 1.0
            if self.b_turn:
                reward = -1.0
            return ("".join(self.board.reshape(-1)), reward, True)
        
    def move(self, same_turn=False):
        if not same_turn:
            recent_move = []
            recent_capture = []
        else:
            recent_move = self.history.move_positions[self.history.step-1]
            recent_capture = self.history.capture_positions[self.history.step-1]
            
        idxs = [i for i,j in self.pieces.items() if len(j.moves) > 0]
            
#         print(idxs)
        capture = False
        recent_move = []
        if len(idxs) > 0:
            i = np.random.randint(len(idxs))
#             print(idxs[i])
            moves = self.pieces[idxs[i]].moves
            j = np.random.randint(len(moves))
#             print(i, moves, j, moves[j])
#             print(idxs[i], self.pieces[idxs[i]].position, "->", moves[j])
#             self.board[self.positions[idxs[i]]] = '0'
#             self.board[moves[j]] = symbol
            
#             print(self.pieces[idxs[i]].priority)
            if self.pieces[idxs[i]].priority:
#                 print('jump')
                enemy_x = (self.pieces[idxs[i]].position[0]+moves[j][0])/2
                enemy_y = (self.pieces[idxs[i]].position[1]+moves[j][1])/2
                capture = True
                recent_capture.append((enemy_x, enemy_y))
                for k,v in self.pieces.items():
                    if (enemy_x, enemy_y) == v.position:
                        v.live = False
                        v.position = (-1,-1)
                        v.moves = []

            recent_move.append(self.pieces[idxs[i]].position)
            self.history.add(recent_capture, recent_move, moves[j], not same_turn)
            
            self.pieces[idxs[i]].position = moves[j]
            if self.pieces[idxs[i]].is_b and self.pieces[idxs[i]].position[0] == 0:
#                 print('king!')
                self.pieces[idxs[i]].is_king = True
                self.pieces[idxs[i]].symbol = 'B'
            if not self.pieces[idxs[i]].is_b and self.pieces[idxs[i]].position[0] == 7:
#                 print('king!')
                self.pieces[idxs[i]].is_king = True
                self.pieces[idxs[i]].symbol = 'R'
            
            self.update_board()
            self.free_moves()

            if not(capture and self.pieces[idxs[i]].priority):
#                 print('change turn')
                self.b_turn = not self.b_turn
                self.history.save_board(self.board)
                self.free_moves()
            else:
                self.move(True)
                
            return ("".join(self.board.reshape(-1)), 0.0, False)
                
        else:
            reward = 1.0
            print("can't move!")
            if self.b_turn:
                print('red wins!')
                reward = -1.0
            else:
                print('black wins!')
                
            return ("".join(self.board.reshape(-1)), reward, True)
        
    def free_moves(self):
        for i,j in self.pieces.items():
            if j.live:
                moves = []
                priority = False
                if j.is_b:
                    enemy = 'r'
                    enemy_king = 'R'
                else:
                    enemy = 'b'
                    enemy_king = 'B'
                    
                if j.is_b == True or j.is_king:
        #             print(i, self.pieces[i].position, self.board[self.pieces[i].position])
                    up_left = (j.position[0]-1,j.position[1]-1)
                    up_right = (j.position[0]-1,j.position[1]+1)
                    up_2_left = (j.position[0]-2,j.position[1]-2)
                    up_2_right = (j.position[0]-2,j.position[1]+2)
        #             print(up_right, up_left)
                    if up_left[0]>-1 and up_left[1]>-1 and \
                        (self.board[up_left]==enemy or self.board[up_left]==enemy_king) and \
                        up_2_left[0]>-1 and up_2_left[1]>-1 and self.board[up_2_left]=='0':
                        moves.append(up_2_left)
                        priority = True
        #                 print('can eat!', up_left, up_2_left)
        #                 print(self.board[down_2_left])
                    if up_right[0]>-1 and up_right[1]<8 and \
                        (self.board[up_right]==enemy or self.board[up_right]==enemy_king) and \
                        up_2_right[0]>-1 and up_2_right[1]<8 and self.board[up_2_right]=='0':
                        moves.append(up_2_right)
                        priority = True
        #                 print('can eat!', up_right, up_2_right)
        #                 print(self.board[down_2_right])
                    if priority == False and up_left[0]>-1 and up_left[1]>-1 and self.board[up_left]=='0':
                        moves.append(up_left)
        #                 print(board[up_left])
                    if priority == False and up_right[0]>-1 and up_right[1]<8 and self.board[up_right]=='0':
                        moves.append(up_right)
        #                 print(self.board[up_right])
        #             print("")
                if j.is_b == False or j.is_king:
        #             print(i, self.pieces[i].position, board[self.pieces[i].position])
                    down_left = (j.position[0]+1,j.position[1]-1)
                    down_right = (j.position[0]+1,j.position[1]+1)
                    down_2_left = (j.position[0]+2,j.position[1]-2)
                    down_2_right = (j.position[0]+2,j.position[1]+2)
        #             print(down_right, down_left)
                    if down_left[0]<8 and down_left[1]>-1 and \
                        (self.board[down_left]==enemy or self.board[down_left]==enemy_king) and \
                        down_2_left[0]<8 and down_2_left[1]>-1 and self.board[down_2_left]=='0':
                        if j.is_king and priority == False:
                            moves = []
                        moves.append(down_2_left)
                        priority = True
        #                 print('can eat!')
        #                 print(self.board[down_2_left])
                    if down_right[0]<8 and down_right[1]<8 and \
                        (self.board[down_right]==enemy or self.board[down_right]==enemy_king) and \
                        down_2_right[0]<8 and down_2_right[1]<8 and self.board[down_2_right]=='0':
                        if j.is_king and priority == False:
                            moves = []
                        moves.append(down_2_right)
                        priority = True
        #                 print('can eat!')
        #                 print(self.board[down_2_right])
                    if priority == False and down_left[0]<8 and down_left[1]>-1 and self.board[down_left]=='0':
                        moves.append(down_left)
        #                 print(self.board[down_left])
                    if priority == False and down_right[0]<8 and down_right[1]<8 and self.board[down_right]=='0':
                        moves.append(down_right)
        #                 print(self.board[down_right])
        #             print("")
                j.priority = priority
                j.moves = moves
        
        if self.b_turn:
            idxs = [i for i,j in self.pieces.items() if i >= 12 and j.priority and j.live]
            if len(idxs) == 0:
                idxs = [i for i,j in self.pieces.items() if i >= 12 and j.live]
#                 print('not priorities')
        else:
            idxs = [i for i,j in self.pieces.items() if i < 12 and j.priority and j.live]
            if len(idxs) == 0:
                idxs = [i for i,j in self.pieces.items() if i < 12 and j.live]
#                 print('not priorities')

#         print(idxs)

        for i,j in self.pieces.items():
            if not i in idxs:
                j.priority = False
                j.moves = []
        
        return len(idxs) > 0
    
    def update_board(self):
        shape = (8,8)
        board = np.full(shape, '0')
        for i,j in self.pieces.items():
            if j.live:
                board[j.position] = j.symbol
        self.board = board
        
    def print_gui_board(self, step=None):
        if step == None:
            board = self.board
            step = self.history.step-1
        else:
            board = self.history.board[step]
            
        if step == -1:
            final_position = (1,1)
            capture_positions = []
            move_positions = []
        else:
            final_position = self.history.final_position[step]
            capture_positions = self.history.capture_positions[step]
            move_positions = self.history.move_positions[step]
            
        size = 9
        for i in range(size-1):
            for j in range(size):
                if j == size-1:
                    print("")
                elif board[i,j] != '0':
                    if (i,j) == final_position:
                        print("\x1b[31m{}\x1b[0m".format(board[i,j]), end="")
                    else:
                        print(board[i,j], end="")
                elif (i,j) in capture_positions:
                    print("\x1b[31m{}\x1b[0m".format("X"), end="")
                elif (i,j) in move_positions:
                    print("\x1b[31m{}\x1b[0m".format("█"), end="")
                elif (i%2 == 1 and j%2 == 0) or (i%2 == 0 and j%2 == 1):
                    print("▓", end="")
                elif (i%2 == 0 and j%2 == 0) or (i%2 == 1 and j%2 == 1):
                    print("░", end="")
        
    def print_board(self):
        print(self.board)
        
    def print_info(self):
        pieces = game.free_moves()
        print('id', 'position', 'moves', 'priority')
        for i in pieces:
            print(i, pieces[i].position, pieces[i].moves, pieces[i].priority)
            
    def print_previous_board(self, step):
        if step >= 0 and step < self.history.step:
            self.print_gui_board(step)
        else:
            print("step not valid!")
        
    def print_all_previous_board(self):
        for i in range(self.history.step):
            self.print_gui_board(i)
            print("")

In [5]:
import copy

In [6]:
def random_policy(game):
    actions = []
    for i,j in game.pieces.items():
        if len(j.moves) > 0:
            for k in range(len(j.moves)):
                actions.append((i,k))
    if len(actions) > 0:
        return actions[np.random.randint(len(actions))]
    else:
        return None

In [41]:
def policy(new_policy, new_policy_size, board_ids, actions, final_reward, steps):
    for i in range(len(board_ids)-2,-1,-1):
#         print(i)
#         print(board_ids[i])
#         print(actions[i])
#         print(rewards[i])
#         print(steps)
        if not board_ids[i] in new_policy:
            action = {}
            action[actions[i]] = final_reward*(i/steps)
            new_policy[board_ids[i]] = action
            new_policy_size[board_ids[i]] = {}
            new_policy_size[board_ids[i]][actions[i]] = 1
        else:
            action = new_policy[board_ids[i]]
#             print(board_ids[i])
#             print('before', action)
            if actions[i] in action:
#                 print('found')
                new_policy_size[board_ids[i]][actions[i]] += 1
                action[actions[i]] += (final_reward*(i/steps) - action[actions[i]])/new_policy_size[board_ids[i]][actions[i]]
            else:
                action[actions[i]] = final_reward*(i/steps)
                new_policy_size[board_ids[i]][actions[i]] = 1
#             print('after', action)
            new_policy[board_ids[i]] = action
    return new_policy

In [22]:
def black_wins(policy, game):
    board_id = "".join(game.board.reshape(-1))
    if board_id in policy:
        actions = policy[board_id]
        max_action = 0
        max_value = 0
#         print(actions)
        for i in actions:
#             print(i, actions[i])
            if actions[i] > max_value or max_action == 0:
                max_value = actions[i]
                max_action = i
#             print('max', max_value, max_action)
        if max_value < 0:
            max_action = random_policy(game)
        print('black chooses',max_action)
        return max_action
    else:
        return random_policy(game)

In [52]:
b_wins = 0

for i in range(100):
    game = checkers()
    
    steps = 0
    
    done = False
    while done == False:
        if game.b_turn:
            action = black_wins(new_policy, game)
        else:
            action = random_policy(game)
#         print(action)
        next_state, reward, done = game.move_this(action)

#         game.print_gui_board()
#         print('')
        steps += 1

        if done:
            print(steps)
            if game.b_turn:
                print('red wins!')
            else:
                print('black wins!')
                b_wins += 1
print(b_wins/100)

black chooses (15, 1)
black chooses (18, 0)
black chooses (15, 0)
black chooses (12, 0)
210
black wins!
black chooses (15, 1)
black chooses (13, 0)
black chooses (13, 0)
black chooses (12, 0)
black chooses (18, 0)
black chooses (17, 0)
108
red wins!
black chooses (15, 1)
black chooses (14, 1)
black chooses (13, 0)
black chooses (15, 0)
black chooses (18, 0)
black chooses (18, 0)
48
black wins!
black chooses (15, 1)
black chooses (13, 0)
black chooses (13, 0)
black chooses (17, 0)
black chooses (14, 1)
black chooses (19, 0)
90
red wins!
black chooses (15, 1)
black chooses (13, 0)
black chooses (15, 0)
black chooses (13, 1)
black chooses (12, 0)
black chooses (14, 0)
76
red wins!
black chooses (15, 1)
black chooses (13, 0)
black chooses (14, 0)
black chooses (17, 0)
black chooses (22, 0)
121
black wins!
black chooses (15, 1)
black chooses (18, 0)
black chooses (13, 0)
black chooses (13, 0)
63
red wins!
black chooses (15, 1)
black chooses (13, 0)
black chooses (14, 0)
black chooses (17, 1

38
black wins!
black chooses (15, 1)
black chooses (13, 0)
black chooses (14, 0)
black chooses (18, 0)
black chooses (15, 0)
47
red wins!
black chooses (15, 1)
black chooses (13, 0)
black chooses (15, 0)
black chooses (13, 1)
black chooses (14, 0)
black chooses (14, 0)
black chooses (19, 0)
150
red wins!
black chooses (15, 1)
black chooses (13, 0)
black chooses (14, 0)
black chooses (17, 1)
black chooses (18, 0)
black chooses (22, 0)
black chooses (13, 1)
black chooses (12, 0)
100
red wins!
black chooses (15, 1)
black chooses (18, 0)
black chooses (12, 0)
black chooses (16, 0)
46
black wins!
black chooses (15, 1)
black chooses (13, 0)
black chooses (14, 0)
black chooses (19, 0)
42
red wins!
black chooses (15, 1)
black chooses (18, 0)
black chooses (18, 0)
black chooses (22, 0)
52
black wins!
black chooses (15, 1)
black chooses (18, 0)
black chooses (14, 1)
black chooses (14, 0)
85
red wins!
black chooses (15, 1)
black chooses (18, 0)
black chooses (12, 0)
black chooses (16, 0)
76
black

In [38]:
new_policy = np.load('new_policy.npy').item()

In [53]:
print(len(new_policy))
np.save('new_policy', new_policy)

1624138


In [50]:
# new_policy = {}
# new_policy_size = {}

for i in range(100000):
    print(i)
    game = checkers()
    steps = 0

    board_ids = []
    actions = []
    
    board_ids.append("".join(game.board.reshape(-1)))
    
    done = False
    while done == False:

        action = random_policy(game)
        next_state, reward, done = game.move_this(action)
#         game.print_gui_board()
#             print(steps)

        if action != None:
            steps += 1
            board_ids.append("".join(game.board.reshape(-1)))
            actions.append(action)
#             game.print_gui_board()
            
        if steps > 50:
            print('break')
            break
#     print(board_ids[0])
    if done:
        new_policy = policy(new_policy, new_policy_size, board_ids, actions, reward, steps)
#     print(new_policy)

0
break
1
break
2
break
3
4
break
5
break
6
7
break
8
break
9
10
break
11
break
12
break
13
14
break
15
16
17
break
18
break
19
break
20
break
21
22
break
23
break
24
25
break
26
break
27
break
28
29
break
30
break
31
break
32
33
break
34
break
35
break
36
break
37
38
break
39
break
40
break
41
42
43
break
44
break
45
break
46
break
47
48
break
49
break
50
break
51
break
52
53
break
54
break
55
56
57
58
break
59
break
60
61
break
62
break
63
break
64
65
break
66
break
67
68
break
69
70
break
71
break
72
break
73
break
74
75
break
76
77
78
break
79
80
break
81
82
break
83
break
84
break
85
86
87
88
89
break
90
break
91
break
92
break
93
break
94
break
95
break
96
break
97
break
98
break
99
100
break
101
break
102
break
103
break
104
105
break
106
break
107
108
break
109
break
110
break
111
112
break
113
114
break
115
116
break
117
118
break
119
120
121
break
122
break
123
124
125
126
break
127
128
129
break
130
break
131
132
133
break
134
break
135
136
break
137
break
138
break
139
brea

break
1071
break
1072
break
1073
1074
break
1075
break
1076
break
1077
1078
1079
1080
1081
break
1082
break
1083
break
1084
break
1085
break
1086
break
1087
1088
1089
1090
break
1091
break
1092
break
1093
1094
1095
break
1096
break
1097
1098
1099
1100
1101
break
1102
break
1103
break
1104
break
1105
1106
break
1107
break
1108
1109
1110
1111
1112
break
1113
break
1114
break
1115
break
1116
break
1117
1118
break
1119
break
1120
break
1121
break
1122
break
1123
1124
break
1125
break
1126
break
1127
break
1128
break
1129
break
1130
break
1131
1132
break
1133
1134
break
1135
break
1136
break
1137
break
1138
break
1139
break
1140
break
1141
break
1142
1143
1144
break
1145
break
1146
break
1147
break
1148
break
1149
break
1150
break
1151
break
1152
break
1153
break
1154
1155
break
1156
break
1157
break
1158
1159
1160
break
1161
break
1162
break
1163
break
1164
break
1165
break
1166
1167
1168
1169
break
1170
break
1171
break
1172
1173
break
1174
1175
1176
1177
1178
1179
break
1180
1181
1182
11

2023
2024
2025
break
2026
break
2027
2028
break
2029
break
2030
2031
2032
break
2033
break
2034
2035
2036
break
2037
break
2038
break
2039
break
2040
break
2041
break
2042
break
2043
2044
break
2045
break
2046
break
2047
2048
break
2049
break
2050
2051
break
2052
break
2053
2054
break
2055
2056
break
2057
break
2058
2059
break
2060
break
2061
break
2062
break
2063
2064
break
2065
2066
break
2067
2068
break
2069
break
2070
break
2071
break
2072
2073
break
2074
2075
2076
break
2077
2078
2079
2080
break
2081
break
2082
2083
break
2084
2085
2086
break
2087
break
2088
break
2089
2090
break
2091
break
2092
break
2093
break
2094
break
2095
break
2096
2097
2098
2099
break
2100
2101
break
2102
2103
break
2104
break
2105
2106
break
2107
break
2108
break
2109
break
2110
break
2111
break
2112
break
2113
break
2114
break
2115
break
2116
break
2117
break
2118
break
2119
2120
break
2121
break
2122
2123
break
2124
break
2125
break
2126
break
2127
break
2128
break
2129
2130
2131
break
2132
2133
2134
br

break
2954
2955
break
2956
break
2957
break
2958
break
2959
break
2960
2961
break
2962
break
2963
break
2964
break
2965
2966
break
2967
break
2968
2969
break
2970
break
2971
2972
2973
break
2974
2975
2976
break
2977
break
2978
2979
break
2980
break
2981
2982
break
2983
2984
break
2985
break
2986
2987
2988
2989
2990
2991
2992
break
2993
2994
break
2995
break
2996
2997
2998
break
2999
break
3000
3001
3002
break
3003
break
3004
break
3005
3006
break
3007
break
3008
break
3009
3010
break
3011
break
3012
break
3013
break
3014
break
3015
break
3016
break
3017
break
3018
break
3019
break
3020
break
3021
3022
3023
break
3024
break
3025
break
3026
break
3027
3028
break
3029
3030
3031
break
3032
break
3033
break
3034
break
3035
3036
break
3037
3038
3039
break
3040
break
3041
break
3042
break
3043
break
3044
break
3045
break
3046
3047
3048
3049
3050
break
3051
3052
break
3053
break
3054
3055
break
3056
break
3057
3058
break
3059
break
3060
3061
break
3062
break
3063
3064
break
3065
3066
break
306

break
3889
3890
break
3891
break
3892
3893
break
3894
break
3895
3896
break
3897
break
3898
3899
break
3900
break
3901
break
3902
break
3903
break
3904
break
3905
3906
3907
break
3908
break
3909
break
3910
break
3911
break
3912
break
3913
3914
break
3915
break
3916
break
3917
3918
3919
break
3920
3921
3922
3923
break
3924
3925
break
3926
break
3927
break
3928
3929
3930
3931
break
3932
break
3933
break
3934
break
3935
3936
break
3937
break
3938
break
3939
3940
3941
break
3942
break
3943
break
3944
3945
break
3946
break
3947
break
3948
break
3949
3950
break
3951
3952
break
3953
3954
break
3955
break
3956
3957
break
3958
break
3959
3960
break
3961
break
3962
break
3963
3964
break
3965
3966
3967
break
3968
break
3969
break
3970
break
3971
break
3972
break
3973
3974
break
3975
break
3976
break
3977
break
3978
3979
break
3980
3981
break
3982
break
3983
3984
break
3985
break
3986
break
3987
3988
3989
3990
break
3991
3992
break
3993
3994
3995
3996
3997
break
3998
break
3999
break
4000
break
40

...

break
95993
break
95994
break
95995
break
95996
break
95997
95998
95999
96000
break
96001
break
96002
96003
96004
96005
break
96006
96007
break
96008
break
96009
break
96010
break
96011
break
96012
break
96013
96014
break
96015
96016
96017
break
96018
break
96019
break
96020
break
96021
break
96022
break
96023
96024
break
96025
break
96026
break
96027
break
96028
96029
break
96030
96031
break
96032
96033
96034
break
96035
break
96036
break
96037
96038
96039
break
96040
96041
96042
96043
96044
96045
break
96046
96047
break
96048
break
96049
break
96050
break
96051
96052
break
96053
break
96054
96055
96056
break
96057
break
96058
break
96059
break
96060
96061
break
96062
break
96063
96064
96065
96066
break
96067
96068
break
96069
break
96070
break
96071
break
96072
break
96073
break
96074
break
96075
break
96076
break
96077
break
96078
break
96079
break
96080
break
96081
break
96082
break
96083
break
96084
break
96085
96086
96087
96088
96089
96090
break
96091
break
96092
96093
96094
brea

break
96854
break
96855
break
96856
96857
break
96858
96859
96860
break
96861
break
96862
break
96863
break
96864
break
96865
break
96866
96867
96868
96869
break
96870
96871
break
96872
96873
96874
break
96875
break
96876
break
96877
break
96878
break
96879
break
96880
break
96881
break
96882
break
96883
96884
break
96885
break
96886
break
96887
96888
break
96889
96890
96891
break
96892
96893
96894
break
96895
96896
break
96897
break
96898
break
96899
96900
break
96901
96902
break
96903
break
96904
break
96905
break
96906
96907
96908
96909
break
96910
break
96911
break
96912
break
96913
break
96914
break
96915
break
96916
break
96917
break
96918
break
96919
break
96920
96921
break
96922
96923
break
96924
break
96925
96926
break
96927
break
96928
96929
break
96930
break
96931
break
96932
break
96933
break
96934
96935
break
96936
96937
break
96938
break
96939
break
96940
break
96941
break
96942
break
96943
96944
96945
break
96946
break
96947
96948
96949
break
96950
96951
break
96952
9695

break
97704
97705
break
97706
break
97707
97708
break
97709
break
97710
break
97711
break
97712
break
97713
break
97714
97715
97716
break
97717
97718
97719
97720
break
97721
break
97722
break
97723
break
97724
97725
break
97726
break
97727
97728
break
97729
break
97730
break
97731
97732
break
97733
break
97734
break
97735
break
97736
break
97737
break
97738
97739
break
97740
break
97741
break
97742
97743
97744
break
97745
break
97746
97747
97748
break
97749
break
97750
break
97751
97752
break
97753
97754
97755
break
97756
break
97757
97758
break
97759
break
97760
break
97761
break
97762
break
97763
break
97764
97765
97766
97767
break
97768
97769
97770
97771
break
97772
97773
break
97774
break
97775
97776
break
97777
97778
break
97779
break
97780
break
97781
97782
break
97783
97784
break
97785
break
97786
break
97787
97788
97789
97790
break
97791
97792
break
97793
97794
break
97795
break
97796
break
97797
break
97798
break
97799
break
97800
97801
break
97802
break
97803
break
97804
9780

break
98546
break
98547
98548
98549
break
98550
break
98551
break
98552
break
98553
break
98554
break
98555
98556
break
98557
98558
98559
98560
98561
98562
break
98563
break
98564
break
98565
98566
break
98567
break
98568
98569
break
98570
break
98571
break
98572
break
98573
break
98574
98575
break
98576
break
98577
98578
break
98579
break
98580
break
98581
break
98582
break
98583
break
98584
98585
98586
98587
98588
98589
break
98590
break
98591
break
98592
break
98593
break
98594
break
98595
break
98596
98597
98598
break
98599
break
98600
98601
break
98602
98603
98604
break
98605
break
98606
break
98607
break
98608
break
98609
break
98610
break
98611
98612
98613
break
98614
98615
98616
break
98617
98618
98619
break
98620
98621
98622
break
98623
break
98624
break
98625
98626
break
98627
break
98628
break
98629
break
98630
break
98631
break
98632
break
98633
break
98634
98635
98636
break
98637
break
98638
break
98639
98640
98641
break
98642
break
98643
break
98644
break
98645
break
9864

99372
99373
break
99374
break
99375
99376
break
99377
break
99378
99379
break
99380
break
99381
99382
99383
break
99384
break
99385
break
99386
break
99387
break
99388
99389
break
99390
break
99391
99392
break
99393
break
99394
99395
break
99396
99397
break
99398
99399
99400
break
99401
break
99402
99403
99404
99405
break
99406
break
99407
99408
break
99409
break
99410
break
99411
break
99412
99413
break
99414
break
99415
break
99416
break
99417
break
99418
99419
break
99420
break
99421
break
99422
99423
break
99424
break
99425
break
99426
break
99427
99428
break
99429
99430
break
99431
break
99432
99433
99434
break
99435
break
99436
99437
99438
break
99439
break
99440
break
99441
99442
break
99443
break
99444
break
99445
99446
break
99447
99448
break
99449
99450
break
99451
break
99452
break
99453
break
99454
99455
99456
99457
99458
99459
99460
break
99461
break
99462
break
99463
99464
break
99465
break
99466
break
99467
break
99468
break
99469
break
99470
99471
break
99472
break
9947

In [28]:
states = {}

game = checkers()

def create_env(game):
    games = []
    board_id = "".join(game.board.reshape(-1))
    if not board_id in states:
#         game.print_gui_board()
        actions = {}
        n_actions = 0
        for i,j in game.pieces.items():
            if len(j.moves) > 0:
                n_actions += len(j.moves)
#         print(n_actions)
        for i,j in game.pieces.items():
            if len(j.moves) > 0:
                actions[i] = []
                for k in range(len(j.moves)):
#                     print(i, j.position, j.moves)
#                     print(i, k)
                    cpy = copy.deepcopy(game)
                    actions[i].append((1/n_actions,)+cpy.move_this(i,k))
                    games.append(cpy)
        states[board_id] = actions
    else:
#         game.print_gui_board()
        print("end")
    return games

n_turns = 100
games = [game]
for i in range(n_turns):
    for j in range(len(games)):
        games += create_env(games[j])
        games.pop(0)
        print('n_games', len(games))
#         print(games)
# print(states)

TypeError: move_this() takes 2 positional arguments but 3 were given

In [45]:
# states = {}

game = checkers()
del states["".join(game.board.reshape(-1))]

def create_env(game):
    board_id = "".join(game.board.reshape(-1))
    if not board_id in states:
        game.print_gui_board()
        actions = {}
        for i,j in game.pieces.items():
            if len(j.moves) > 0:
                n_actions = len(j.moves)
                actions[i] = []
                for k in range(n_actions):
                    print(i, j.position, j.moves)
                    print(i, k)
                    cpy = copy.deepcopy(game)
                    actions[i].append((1/n_actions,)+cpy.move_this(i,k))
        states[board_id] = actions
        for i in actions:
#             print(i, actions[i])
            for j in range(len(actions[i])):
                next_state = actions[i][j][1]
#                 print(j, next_state)
                if next_state not in states:
                    cpy = copy.deepcopy(game)
                    cpy.move_this(i,j)
                    create_env(cpy)
    else:
#         game.print_gui_board()
        print("end")

create_env(game)
# print(states)

░r░r░r░r
r░r░r░r░
░r░r░r░r
▓░▓░▓░▓░
░▓░▓░▓░▓
b░b░b░b░
░b░b░b░b
b░b░b░b░
12 (5, 0) [(4, 1)]
12 0
change turn
13 (5, 2) [(4, 1), (4, 3)]
13 0
change turn
13 (5, 2) [(4, 1), (4, 3)]
13 1
change turn
14 (5, 4) [(4, 3), (4, 5)]
14 0
change turn
14 (5, 4) [(4, 3), (4, 5)]
14 1
change turn
15 (5, 6) [(4, 5), (4, 7)]
15 0
change turn
15 (5, 6) [(4, 5), (4, 7)]
15 1
change turn
change turn
░r░r░r░r
r░r░r░r░
░r░r░r░r
▓░▓░▓░▓░
░▓░b░▓░▓
b░█░b░b░
░b░b░b░b
b░b░b░b░
8 (2, 1) [(3, 0), (3, 2)]
8 0
change turn
8 (2, 1) [(3, 0), (3, 2)]
8 1
change turn
9 (2, 3) [(3, 2), (3, 4)]
9 0
change turn
9 (2, 3) [(3, 2), (3, 4)]
9 1
change turn
10 (2, 5) [(3, 4), (3, 6)]
10 0
change turn
10 (2, 5) [(3, 4), (3, 6)]
10 1
change turn
11 (2, 7) [(3, 6)]
11 0
change turn
change turn
░r░r░r░r
r░r░r░r░
░█░r░r░r
r░▓░▓░▓░
░▓░b░▓░▓
b░▓░b░b░
░b░b░b░b
b░b░b░b░
12 (5, 0) [(4, 1)]
12 0
change turn
13 (4, 3) [(3, 2), (3, 4)]
13 0
change turn
13 (4, 3) [(3, 2), (3, 4)]
13 1
change turn
14 (5, 4) [(4, 5)]
14 0
change turn
15 (5, 6

░▓░▓░r░r
▓░b░▓░▓░
░X░▓░r░▓
█░▓░▓░▓░
░▓░▓░b░b
b░▓░b░b░
6 (1, 4) [(2, 3)]
6 0
change turn
9 (4, 5) [(5, 4), (5, 6)]
9 0
change turn
9 (4, 5) [(5, 4), (5, 6)]
9 1
change turn
10 (2, 5) [(3, 4), (3, 6)]
10 0
change turn
10 (2, 5) [(3, 4), (3, 6)]
10 1
change turn
11 (2, 7) [(3, 6)]
11 0
change turn
change turn
░▓░▓░r░r
▓░b░█░r░
░▓░r░r░r
▓░b░▓░▓░
░▓░▓░r░▓
▓░▓░▓░▓░
░▓░▓░b░b
b░▓░b░b░
21 (3, 2) [(1, 4)]
21 0
change turn
change turn
░▓░▓░r░r
▓░b░b░r░
░▓░X░r░r
▓░█░▓░▓░
░▓░▓░r░▓
▓░▓░▓░▓░
░▓░▓░b░b
b░▓░b░b░
2 (0, 5) [(2, 3)]
2 0
change turn
change turn
░▓░▓░█░r
▓░b░X░r░
░▓░r░r░r
▓░▓░▓░▓░
░▓░▓░r░▓
▓░▓░▓░▓░
░▓░▓░b░b
b░▓░b░b░
16 (1, 2) [(0, 1), (0, 3)]
16 0
change turn
16 (1, 2) [(0, 1), (0, 3)]
16 1
change turn
18 (6, 5) [(5, 4), (5, 6)]
18 0
change turn
18 (6, 5) [(5, 4), (5, 6)]
18 1
change turn
19 (6, 7) [(5, 6)]
19 0
change turn
20 (7, 0) [(6, 1)]
20 0
change turn
22 (7, 4) [(6, 3)]
22 0
change turn
change turn
░B░▓░▓░r
▓░█░▓░r░
░▓░r░r░r
▓░▓░▓░▓░
░▓░▓░r░▓
▓░▓░▓░▓░
░▓░▓░b░b
b░▓░b░b░
2 (2, 3) [(3, 

B░▓░▓░▓░
░▓░▓░▓░r
▓░▓░r░▓░
░▓░▓░▓░▓
▓░b░█░▓░
░▓░r░▓░b
▓░▓░b░b░
16 (1, 0) [(0, 1), (2, 1)]
16 0
change turn
16 (1, 0) [(0, 1), (2, 1)]
16 1
change turn
19 (6, 7) [(5, 6)]
19 0
change turn
20 (5, 2) [(4, 1), (4, 3)]
20 0
change turn
20 (5, 2) [(4, 1), (4, 3)]
20 1
change turn
22 (7, 4) [(6, 5)]
22 0
change turn
23 (7, 6) [(6, 5)]
23 0
change turn
change turn
░B░▓░▓░▓
█░▓░▓░▓░
░▓░▓░▓░r
▓░▓░r░▓░
░▓░▓░▓░▓
▓░b░▓░▓░
░▓░r░▓░b
▓░▓░b░b░
3 (6, 3) [(7, 2)]
3 0
change turn
7 (3, 4) [(4, 3), (4, 5)]
7 0
change turn
7 (3, 4) [(4, 3), (4, 5)]
7 1
change turn
11 (2, 7) [(3, 6)]
11 0
change turn
change turn
░B░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░r
▓░▓░r░▓░
░▓░▓░▓░▓
▓░b░▓░▓░
░▓░█░▓░b
▓░R░b░b░
16 (0, 1) [(1, 0), (1, 2)]
16 0
change turn
16 (0, 1) [(1, 0), (1, 2)]
16 1
change turn
19 (6, 7) [(5, 6)]
19 0
change turn
20 (5, 2) [(4, 1), (4, 3)]
20 0
change turn
20 (5, 2) [(4, 1), (4, 3)]
20 1
change turn
22 (7, 4) [(6, 3), (6, 5)]
22 0
change turn
22 (7, 4) [(6, 3), (6, 5)]
22 1
change turn
23 (7, 6) [(6, 5)]
23 0
change 

B░▓░▓░█░
░▓░▓░▓░r
▓░▓░▓░▓░
░▓░r░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░b
▓░▓░b░b░
16 (1, 0) [(0, 1), (2, 1)]
16 0
change turn
16 (1, 0) [(0, 1), (2, 1)]
16 1
change turn
19 (6, 7) [(5, 6)]
19 0
change turn
22 (7, 4) [(6, 3), (6, 5)]
22 0
change turn
22 (7, 4) [(6, 3), (6, 5)]
22 1
change turn
23 (7, 6) [(6, 5)]
23 0
change turn
change turn
░B░▓░R░▓
█░▓░▓░▓░
░▓░▓░▓░r
▓░▓░▓░▓░
░▓░r░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░b
▓░▓░b░b░
3 (0, 5) [(1, 4), (1, 6)]
3 0
change turn
3 (0, 5) [(1, 4), (1, 6)]
3 1
change turn
7 (4, 3) [(5, 2), (5, 4)]
7 0
change turn
7 (4, 3) [(5, 2), (5, 4)]
7 1
change turn
11 (2, 7) [(3, 6)]
11 0
change turn
change turn
░B░▓░█░▓
▓░▓░R░▓░
░▓░▓░▓░r
▓░▓░▓░▓░
░▓░r░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░b
▓░▓░b░b░
16 (0, 1) [(1, 0), (1, 2)]
16 0
change turn
16 (0, 1) [(1, 0), (1, 2)]
16 1
change turn
19 (6, 7) [(5, 6)]
19 0
change turn
22 (7, 4) [(6, 3), (6, 5)]
22 0
change turn
22 (7, 4) [(6, 3), (6, 5)]
22 1
change turn
23 (7, 6) [(6, 5)]
23 0
change turn
change turn
░█░▓░▓░▓
B░▓░R░▓░
░▓░▓░▓░r
▓░▓░▓░▓░
░▓░r░▓░▓
▓░▓░▓░▓░
░▓░

change turn
19 (6, 7) [(5, 6)]
19 0
change turn
22 (7, 4) [(6, 3), (6, 5)]
22 0
change turn
22 (7, 4) [(6, 3), (6, 5)]
22 1
change turn
23 (7, 6) [(6, 5)]
23 0
change turn
change turn
░▓░▓░▓░▓
B░▓░▓░▓░
░█░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░r░▓
▓░▓░▓░▓░
░▓░▓░▓░b
▓░▓░b░b░
11 (4, 5) [(5, 4), (5, 6)]
11 0
change turn
11 (4, 5) [(5, 4), (5, 6)]
11 1
change turn
change turn
░▓░▓░▓░▓
B░▓░▓░▓░
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░█░▓
▓░▓░r░▓░
░▓░▓░▓░b
▓░▓░b░b░
16 (1, 0) [(0, 1), (2, 1)]
16 0
change turn
16 (1, 0) [(0, 1), (2, 1)]
16 1
change turn
19 (6, 7) [(5, 6)]
19 0
change turn
22 (7, 4) [(6, 3), (6, 5)]
22 0
change turn
22 (7, 4) [(6, 3), (6, 5)]
22 1
change turn
23 (7, 6) [(6, 5)]
23 0
change turn
change turn
░B░▓░▓░▓
█░▓░▓░▓░
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
▓░▓░r░▓░
░▓░▓░▓░b
▓░▓░b░b░
11 (5, 4) [(6, 3), (6, 5)]
11 0
change turn
11 (5, 4) [(6, 3), (6, 5)]
11 1
change turn
change turn
░B░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
▓░▓░█░▓░
░▓░r░▓░b
▓░▓░b░b░
22 (7, 4) [(5, 2)]
22 0
change turn
change turn
░B░▓░▓░▓
▓░▓░▓░▓░
░▓

...

change turn
change turn
░▓░▓░▓░▓
▓░B░▓░▓░
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░█░▓
B░▓░R░▓░
░▓░▓░▓░▓
▓░▓░▓░▓░
19 (1, 2) [(0, 1), (0, 3), (2, 1), (2, 3)]
19 0
change turn
19 (1, 2) [(0, 1), (0, 3), (2, 1), (2, 3)]
19 1
change turn
19 (1, 2) [(0, 1), (0, 3), (2, 1), (2, 3)]
19 2
change turn
19 (1, 2) [(0, 1), (0, 3), (2, 1), (2, 3)]
19 3
change turn
23 (5, 0) [(4, 1), (6, 1)]
23 0
change turn
23 (5, 0) [(4, 1), (6, 1)]
23 1
change turn
change turn
░▓░B░▓░▓
▓░█░▓░▓░
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
B░▓░R░▓░
░▓░▓░▓░▓
▓░▓░▓░▓░
11 (5, 4) [(4, 3), (4, 5), (6, 3), (6, 5)]
11 0
change turn
11 (5, 4) [(4, 3), (4, 5), (6, 3), (6, 5)]
11 1
change turn
11 (5, 4) [(4, 3), (4, 5), (6, 3), (6, 5)]
11 2
change turn
11 (5, 4) [(4, 3), (4, 5), (6, 3), (6, 5)]
11 3
change turn
change turn
░▓░B░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░R░▓
B░▓░█░▓░
░▓░▓░▓░▓
▓░▓░▓░▓░
19 (0, 3) [(1, 2), (1, 4)]
19 0
change turn
19 (0, 3) [(1, 2), (1, 4)]
19 1
change turn
23 (5, 0) [(4, 1), (6, 1)]
23 0
change turn
23 (5, 0) [(4, 1), (6, 1)]
23 1
chan

▓░▓░▓░▓░
19 (5, 2) [(4, 1), (4, 3), (6, 3)]
19 0
change turn
19 (5, 2) [(4, 1), (4, 3), (6, 3)]
19 1
change turn
19 (5, 2) [(4, 1), (4, 3), (6, 3)]
19 2
change turn
23 (6, 1) [(5, 0), (7, 0), (7, 2)]
23 0
change turn
23 (6, 1) [(5, 0), (7, 0), (7, 2)]
23 1
change turn
23 (6, 1) [(5, 0), (7, 0), (7, 2)]
23 2
change turn
change turn
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░R░▓
▓░▓░▓░▓░
░▓░B░▓░▓
▓░█░▓░▓░
░B░▓░▓░▓
▓░▓░▓░▓░
11 (2, 5) [(1, 4), (1, 6), (3, 4), (3, 6)]
11 0
change turn
11 (2, 5) [(1, 4), (1, 6), (3, 4), (3, 6)]
11 1
change turn
11 (2, 5) [(1, 4), (1, 6), (3, 4), (3, 6)]
11 2
change turn
11 (2, 5) [(1, 4), (1, 6), (3, 4), (3, 6)]
11 3
change turn
change turn
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░█░▓
▓░▓░R░▓░
░▓░B░▓░▓
▓░▓░▓░▓░
░B░▓░▓░▓
▓░▓░▓░▓░
19 (4, 3) [(2, 5)]
19 0
change turn
change turn
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░R░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
▓░█░▓░▓░
░B░B░▓░▓
▓░▓░▓░▓░
11 (2, 5) [(1, 4), (1, 6), (3, 4), (3, 6)]
11 0
change turn
11 (2, 5) [(1, 4), (1, 6), (3, 4), (3, 6)]
11 1
change turn
11 (2, 5) [(1, 4), (1, 6), (3, 

B░▓░▓░▓░
░▓░▓░▓░▓
▓░▓░█░▓░
░B░R░▓░▓
▓░▓░▓░▓░
19 (3, 0) [(2, 1), (4, 1)]
19 0
change turn
19 (3, 0) [(2, 1), (4, 1)]
19 1
change turn
23 (6, 1) [(5, 0), (5, 2), (7, 0), (7, 2)]
23 0
change turn
23 (6, 1) [(5, 0), (5, 2), (7, 0), (7, 2)]
23 1
change turn
23 (6, 1) [(5, 0), (5, 2), (7, 0), (7, 2)]
23 2
change turn
23 (6, 1) [(5, 0), (5, 2), (7, 0), (7, 2)]
23 3
change turn
change turn
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
█░▓░▓░▓░
░B░▓░▓░▓
▓░▓░▓░▓░
░B░R░▓░▓
▓░▓░▓░▓░
11 (6, 3) [(5, 2), (5, 4), (7, 2), (7, 4)]
11 0
change turn
11 (6, 3) [(5, 2), (5, 4), (7, 2), (7, 4)]
11 1
change turn
11 (6, 3) [(5, 2), (5, 4), (7, 2), (7, 4)]
11 2
change turn
11 (6, 3) [(5, 2), (5, 4), (7, 2), (7, 4)]
11 3
change turn
change turn
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
▓░▓░▓░▓░
░B░▓░▓░▓
▓░▓░▓░▓░
░B░█░▓░▓
▓░R░▓░▓░
19 (4, 1) [(3, 0), (3, 2), (5, 0), (5, 2)]
19 0
change turn
19 (4, 1) [(3, 0), (3, 2), (5, 0), (5, 2)]
19 1
change turn
19 (4, 1) [(3, 0), (3, 2), (5, 0), (5, 2)]
19 2
change turn
19 (4, 1) [(3, 0), (3, 2), (5, 0), (5, 

change turn
23 (7, 0) [(6, 1)]
23 0
change turn
change turn
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
R░▓░▓░▓░
░▓░▓░▓░B
▓░▓░▓░█░
░▓░▓░▓░▓
B░▓░▓░▓░
11 (3, 0) [(2, 1), (4, 1)]
11 0
change turn
11 (3, 0) [(2, 1), (4, 1)]
11 1
change turn
change turn
░▓░▓░▓░▓
▓░▓░▓░▓░
░R░▓░▓░▓
█░▓░▓░▓░
░▓░▓░▓░B
▓░▓░▓░▓░
░▓░▓░▓░▓
B░▓░▓░▓░
19 (4, 7) [(3, 6), (5, 6)]
19 0
change turn
19 (4, 7) [(3, 6), (5, 6)]
19 1
change turn
23 (7, 0) [(6, 1)]
23 0
change turn
change turn
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
█░▓░▓░▓░
░R░▓░▓░B
▓░▓░▓░▓░
░▓░▓░▓░▓
B░▓░▓░▓░
19 (4, 7) [(3, 6), (5, 6)]
19 0
change turn
19 (4, 7) [(3, 6), (5, 6)]
19 1
change turn
23 (7, 0) [(6, 1)]
23 0
change turn
change turn
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
▓░▓░▓░▓░
░R░▓░▓░█
▓░▓░▓░B░
░▓░▓░▓░▓
B░▓░▓░▓░
11 (4, 1) [(3, 0), (3, 2), (5, 0), (5, 2)]
11 0
change turn
11 (4, 1) [(3, 0), (3, 2), (5, 0), (5, 2)]
11 1
change turn
11 (4, 1) [(3, 0), (3, 2), (5, 0), (5, 2)]
11 2
change turn
11 (4, 1) [(3, 0), (3, 2), (5, 0), (5, 2)]
11 3
change turn
change turn
░▓░▓░▓░▓
▓░▓░▓░▓░
░▓░▓░▓░▓
▓

RecursionError: maximum recursion depth exceeded while calling a Python object

In [84]:
len(states)

168616

In [ ]:
np.save("states_2", states)

In [547]:
game = checkers()

In [507]:
game.move_this(8,0)
game.print_gui_board()

change turn
░r░r░r░r
r░r░r░r░
░█░r░r░r
r░▓░▓░▓░
░b░▓░▓░▓
▓░b░b░b░
░b░b░b░b
b░b░b░b░


In [506]:
game.print_info()

id position moves priority
0 (0, 1) [] False
1 (0, 3) [] False
2 (0, 5) [] False
3 (0, 7) [] False
4 (1, 0) [] False
5 (1, 2) [] False
6 (1, 4) [] False
7 (1, 6) [] False
8 (2, 1) [(3, 0), (3, 2)] False
9 (2, 3) [(3, 2), (3, 4)] False
10 (2, 5) [(3, 4), (3, 6)] False
11 (2, 7) [(3, 6)] False
12 (4, 1) [] False
13 (5, 2) [] False
14 (5, 4) [] False
15 (5, 6) [] False
16 (6, 1) [] False
17 (6, 3) [] False
18 (6, 5) [] False
19 (6, 7) [] False
20 (7, 0) [] False
21 (7, 2) [] False
22 (7, 4) [] False
23 (7, 6) [] False
